1. Filter image
2. Random 100,000 points
3. Plotly
4. Filter image
5. Histogram Equalization
6. 100,000 points
7. Plotly

In [71]:
import os

In [72]:
import matplotlib
matplotlib.use('Agg')
import matplotlib.pyplot as plt
from ndreg import *
import ndio.remote.neurodata as neurodata
import nibabel as nb

In [73]:
refToken = "ara_ccf2"
refImg = imgDownload(refToken)

In [74]:
refAnnoImg = imgDownload(refToken, channel="annotation")

In [75]:
randValues = np.random.rand(1000,3)
randValues = np.concatenate(([[0,0,0]],randValues))
randCmap = matplotlib.colors.ListedColormap (randValues)

In [76]:
inToken = "Aut1367"
nd = neurodata()

inImg = imgDownload(inToken, resolution=5)

In [77]:
rawestImg = sitk.GetArrayFromImage(inImg)  ##convert to simpleITK image to normal numpy ndarray

In [78]:
print rawestImg.shape

(1225, 912, 595)


## Rawest Plot (100k sampling)

In [79]:
rawestImg = sitk.GetArrayFromImage(inImg)  ##convert to simpleITK image to normal numpy ndarray

In [80]:
## Randomly sample 100k points
import random
x = rawestImg[:,0,0]
y = rawestImg[0,:,0]
z = rawestImg[0,0,:]

# mod by x to get x, mod by y to get y, mod by z to get z

# xdimensions = len(x)
# ydimensions = len(y)
# zdimensions = len(z)
# index = random.sample(xrange(0,xdimensions*ydimensions*zdimensions),100000)  #66473400 is multiplying xshape by yshape by zshape

# X_val = []
# Y_val = []
# Z_val = []

# for i in index:
#     z_val = int(i/(xdimensions*ydimensions))
#     z_rem = i%(xdimensions*ydimensions)
#     y_val = int(z_rem/xdimensions)
#     x_val = int(z_rem/ydimensions)
    
#     X_val.append(x_val)
#     Y_val.append(y_val)
#     Z_val.append(z_val)

# xlist = []
# ylist = []
# zlist = []
xyz = []
for i in range(100000):
    value = 0
    while(value == 0):
        xval = random.sample(xrange(0,xdimensions), 1)[0]
        yval = random.sample(xrange(0,ydimensions), 1)[0]
        zval = random.sample(xrange(0,zdimensions), 1)[0]
        value = rawestImg[xval,yval,zval]
        if [xval, yval, zval] not in xyz and value > 0:
            xyz.append([xval, yval, zval])
        else:
            value = 0
print xyz

[[249, 548, 214], [218, 369, 373], [94, 82, 284], [463, 247, 127], [1087, 430, 439], [1011, 5, 278], [1099, 818, 184], [1036, 374, 526], [929, 103, 221], [1194, 103, 261], [34, 712, 109], [679, 579, 439], [381, 704, 66], [321, 698, 151], [399, 538, 117], [983, 607, 548], [244, 742, 525], [345, 33, 374], [608, 54, 301], [394, 389, 571], [1043, 744, 272], [568, 13, 420], [354, 197, 146], [51, 345, 31], [442, 836, 260], [857, 33, 274], [1028, 342, 404], [854, 908, 76], [1113, 133, 241], [205, 764, 209], [604, 677, 522], [51, 233, 147], [909, 629, 18], [543, 3, 410], [958, 636, 100], [1220, 882, 84], [121, 842, 92], [52, 868, 91], [477, 160, 423], [79, 240, 585], [710, 175, 480], [203, 885, 368], [1214, 196, 214], [495, 40, 104], [617, 635, 341], [158, 181, 273], [207, 243, 467], [1171, 554, 290], [659, 560, 370], [1220, 311, 274], [828, 642, 533], [245, 92, 326], [966, 493, 496], [1079, 883, 117], [1136, 8, 537], [140, 870, 338], [206, 541, 289], [1041, 203, 174], [674, 571, 146], [552, 5

In [81]:
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from plotly import tools
import plotly
plotly.offline.init_notebook_mode()
import plotly.graph_objs as go

# x = X_val
# y = Y_val
# z = Z_val
xlist = []
ylist = []
zlist = []
for i in xyz:
    xlist.append(i[0])
    ylist.append(i[1])
    zlist.append(i[2])
x = xlist
y = ylist
z = zlist

trace1 = go.Scatter3d(
    x = x,
    y = y,
    z = z,
    mode='markers',
    marker=dict(
        size=1.2,
        color='purple',                # set color to an array/list of desired values
        colorscale='Viridis',          # choose a colorscale
        opacity=0.15
    )
)
data = [trace1]
layout = go.Layout(
    margin=dict(
        l=0,
        r=0,
        b=0,
        t=0
    )
)

fig = go.Figure(data=data, layout=layout)
print('Aut1367rawest' + "plotly")
plotly.offline.plot(fig, filename= 'AUT1367rawestluke' + "plotly.html")

Aut1367rawestplotly


'file:///home/tony/AUT1367rawestlukeplotly.html'

## Filter image

In [82]:
## Clean out noise (Filter Image)

(values, bins) = np.histogram(sitk.GetArrayFromImage(inImg), bins=100, range=(0,500))
plt.plot(bins[:-1], values)

counts = np.bincount(values)
maximum = np.argmax(counts)

lowerThreshold = 100 #maximum
upperThreshold = sitk.GetArrayFromImage(inImg).max()+1

filteredImg = sitk.Threshold(inImg,lowerThreshold,upperThreshold,lowerThreshold) - lowerThreshold

## Randomly sample 100k points

In [83]:
filterImg = sitk.GetArrayFromImage(filteredImg)  ##convert to simpleITK image to normal numpy ndarray

In [84]:
print filterImg[0][0]

[ 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  1  1  3  2  1  5  0  0  1  1  8  0  3  7  0  1  0  0  2  6  8 12  0  0  1
  4  0  0  1  2  0  0  0  0  3  2  3  0  4  2  6  3  0  0  6  3  1  4 15  0
  1  0  1 14  1  0  0  5  0  0  8  0  3  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  6  0  8  7  0
  1  5  6  5  2 11  0  7  0  3  9  3  0  0  2  7 15  3  1  4 11  1  1 12  1
  0  0  8  3  6  0  3  5  1  0  1  2  7  2  1  1  7  0  0  6  3  0  4  2  4
  4  1  1  0  0  3  0  4  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0

In [85]:
## Randomly sample 100k points after filtering
x = filterImg[:,0,0]
y = filterImg[0,:,0]
z = filterImg[0,0,:]

# mod by x to get x, mod by y to get y, mod by z to get z

xdimensions = len(x)
ydimensions = len(y)
zdimensions = len(z)
index = random.sample(xrange(0,xdimensions*ydimensions*zdimensions),100000)  #66473400 is multiplying xshape by yshape by zshape

X_val = []
Y_val = []
Z_val = []

for i in index:
    z_val = int(i/(xdimensions*ydimensions))
    z_rem = i%(xdimensions*ydimensions)
    y_val = int(z_rem/xdimensions)
    x_val = int(z_rem/ydimensions)
    
    X_val.append(x_val)
    Y_val.append(y_val)
    Z_val.append(z_val)

xlist = []
ylist = []
zlist = []
for i in range(100000):
    xlist.append(random.sample(xrange(0,xdimensions), 1)[0])
    ylist.append(random.sample(xrange(0,ydimensions), 1)[0])
    zlist.append(random.sample(xrange(0,zdimensions), 1)[0])
print xlist

[548, 154, 573, 316, 544, 293, 1116, 126, 196, 1158, 1029, 1071, 1002, 253, 810, 496, 635, 451, 844, 1193, 862, 629, 74, 959, 769, 716, 778, 551, 916, 692, 909, 733, 158, 578, 136, 1032, 462, 49, 469, 144, 360, 974, 854, 1015, 139, 21, 57, 1119, 50, 843, 1150, 283, 229, 10, 853, 1146, 327, 673, 2, 621, 6, 299, 122, 1080, 236, 876, 242, 976, 525, 414, 1151, 281, 629, 150, 208, 967, 663, 141, 442, 585, 549, 205, 781, 86, 1146, 547, 172, 579, 335, 310, 897, 139, 231, 1129, 388, 1050, 14, 394, 477, 969, 396, 482, 207, 20, 765, 868, 189, 253, 341, 479, 929, 1077, 382, 1181, 170, 422, 259, 639, 1213, 791, 902, 1105, 867, 1149, 1116, 336, 1139, 302, 550, 1006, 322, 106, 1206, 236, 250, 263, 1098, 927, 638, 82, 1123, 822, 1192, 8, 788, 49, 287, 35, 445, 269, 787, 401, 206, 399, 175, 391, 134, 451, 414, 211, 385, 1191, 1144, 661, 914, 969, 361, 528, 1006, 1075, 1186, 1001, 1103, 1107, 1059, 952, 507, 720, 656, 823, 561, 454, 613, 1223, 715, 1188, 74, 532, 76, 599, 1094, 301, 315, 297, 652, 1045

In [86]:
print X_val
print Y_val
print Z_val

print len(X_val)
print len(Y_val)
print len(Z_val)

[821, 98, 907, 199, 280, 104, 700, 538, 952, 353, 1192, 879, 332, 114, 637, 588, 989, 953, 316, 917, 991, 663, 687, 939, 931, 449, 552, 1107, 46, 897, 1046, 1137, 712, 771, 205, 1149, 647, 609, 367, 645, 272, 242, 1100, 1105, 424, 211, 517, 608, 720, 380, 1042, 245, 89, 139, 21, 858, 673, 1019, 458, 158, 988, 1178, 745, 904, 71, 874, 1164, 574, 1011, 314, 1040, 45, 527, 577, 921, 350, 298, 735, 954, 259, 499, 985, 568, 903, 1006, 505, 1139, 793, 903, 880, 989, 147, 461, 96, 595, 528, 132, 668, 230, 372, 656, 1146, 138, 773, 149, 942, 784, 583, 1148, 582, 275, 917, 882, 579, 332, 1201, 929, 435, 20, 441, 590, 283, 79, 502, 842, 87, 838, 1033, 332, 296, 110, 131, 346, 212, 587, 504, 434, 878, 1102, 833, 301, 666, 373, 857, 739, 82, 274, 649, 446, 84, 1211, 942, 820, 905, 587, 438, 1168, 501, 340, 880, 510, 253, 539, 828, 815, 927, 277, 41, 199, 765, 765, 615, 649, 770, 1081, 31, 44, 800, 416, 206, 742, 350, 313, 406, 931, 1183, 484, 277, 719, 677, 104, 731, 988, 541, 195, 1143, 7, 33, 50

UNUSED:  
spacingImg = inImg.GetSpacing()  
spacing = tuple(i * 50 for i in spacingImg)  
print spacingImg  
print spacing  
inImg.SetSpacing(spacingImg)  
inImg_download = inImg  # Aut1367 set to default spacing  
inImg = imgResample(inImg, spacing=refImg.GetSpacing())  
Img_reorient = imgReorient(inImg, "LPS", "RSA") #specific reoriented Aut1367  
inImg_reorient = Img_reorient  
refImg_ds = imgResample(refImg, spacing=spacing)   # atlas downsample 50x

## Plot of 100k data post filtering

In [87]:
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from plotly import tools
import plotly
plotly.offline.init_notebook_mode()
import plotly.graph_objs as go

x = X_val
y = Y_val
z = Z_val

trace1 = go.Scatter3d(
    x = x,
    y = y,
    z = z,
    mode='markers',
    marker=dict(
        size=1.2,
        color='purple',                # set color to an array/list of desired values
        colorscale='Viridis',          # choose a colorscale
        opacity=0.15
    )
)
data = [trace1]
layout = go.Layout(
    margin=dict(
        l=0,
        r=0,
        b=0,
        t=0
    )
)

fig = go.Figure(data=data, layout=layout)
print('Aut1367filter' + "plotly")
plotly.offline.plot(fig, filename= 'AUT1367filter' + "plotly.html")

Aut1367filterplotly


'file:///home/tony/AUT1367filterplotly.html'

## Filter Image Again
Don't do this

## Clean out noise (Filter Image)

(values, bins) = np.histogram(filterImg, bins=100, range=(0,500))
plt.plot(bins[:-1], values)

counts = np.bincount(values)
maximum = np.argmax(counts)

lowerThreshold = maximum
upperThreshold = filterImg.max()+1

filterX2Img = sitk.Threshold(inImg,lowerThreshold,upperThreshold,lowerThreshold) - lowerThreshold

newImg = sitk.GetArrayFromImage(filterX2Img)  ##convert to simpleITK image to normal numpy ndarray

In [88]:
## Histogram Equalization
## Cut from generateHistogram from clarityviz
import cv2
im = filterImg
img = im[:,:,:]
shape = im.shape
#affine = im.get_affine()
x_value = shape[0]
y_value = shape[1]
z_value = shape[2]
#####################################################
imgflat = img.reshape(-1)
#img_grey = np.array(imgflat * 255, dtype = np.uint8)
#img_eq = exposure.equalize_hist(img_grey)#new_img = img_eq.reshape(x_value, y_value, z_value)
#globaleq = nib.Nifti1Image(new_img, np.eye(4))
    
#nb.save(globaleq, '/home/albert/Thumbo/AutAglobaleq.nii')
######################################################
#clahe = cv2.createCLAHE(clipLimit=2.0, tileGridSize=(8,8))
clahe = cv2.createCLAHE(clipLimit=2.0, tileGridSize=(8,8))
img_grey = np.array(imgflat * 255, dtype = np.uint8)
#threshed = cv2.adaptiveThreshold(img_grey, 255, cv2.ADAPTIVE_THRESH_MEAN_C, cv2.THRESH_BINARY, 3, 0)
cl1 = clahe.apply(img_grey)
#cv2.imwrite('clahe_2.jpg',cl1)
#cv2.startWindowThread()
#cv2.namedWindow("adaptive")
#cv2.imshow("adaptive", cl1)
#cv2.imshow("adaptive", threshed)
#plt.imshow(threshed)
localimgflat = cl1 #cl1.reshape(-1)
newer_img = localimgflat.reshape(x_value, y_value, z_value)  ##this is the numpy.ndarray version
localeq = nb.Nifti1Image(newer_img, np.eye(4))

In [89]:
print newer_img.shape

(1225, 912, 595)


## Plotting post filtering/HistEq

In [90]:
x_histeq = newer_img[:,0,0]
y_histeq = newer_img[0,:,0]
z_histeq = newer_img[0,0,:]

## Randomly sample 100k points after filtering

xdimensions = len(x)
ydimensions = len(y)
zdimensions = len(z)
index = random.sample(xrange(0,xdimensions*ydimensions*zdimensions),100000)  #66473400 is multiplying xshape by yshape by zshape

X_val = []
Y_val = []
Z_val = []

for i in index:
    z_val = int(i/(xdimensions*ydimensions))
    z_rem = i%(xdimensions*ydimensions)
    y_val = int(z_rem/xdimensions)
    x_val = int(z_rem/ydimensions)
    
    X_val.append(x_val)
    Y_val.append(y_val)
    Z_val.append(z_val)

xlist = []
ylist = []
zlist = []

for i in range(100000):
    xlist.append(random.sample(xrange(0,xdimensions), 1)[0])
    ylist.append(random.sample(xrange(0,ydimensions), 1)[0])
    zlist.append(random.sample(xrange(0,zdimensions), 1)[0])

for i in index:
    z_val = int(i/(xdimensions*ydimensions))
    z_rem = i%(xdimensions*ydimensions)
    y_val = int(z_rem/xdimensions)
    x_val = int(z_rem/ydimensions)
    
    X_val.append(x_val)
    Y_val.append(y_val)
    Z_val.append(z_val)
    
trace1 = go.Scatter3d(
    x = x,
    y = y,
    z = z,
    mode='markers',
    marker=dict(
        size=1.2,
        color='purple',                # set color to an array/list of desired values
        colorscale='Viridis',          # choose a colorscale
        opacity=0.15
    )
)
data = [trace1]
layout = go.Layout(
    margin=dict(
        l=0,
        r=0,
        b=0,
        t=0
    )
)

fig = go.Figure(data=data, layout=layout)
print('Aut1367postfilterHistEq' + "plotly")
plotly.offline.plot(fig, filename= 'Aut1367postfilterHistEq' + "plotly.html")

Aut1367postfilterHistEqplotly


'file:///home/tony/Aut1367postfilterHistEqplotly.html'

In [92]:
print "done"

done
